# Dataset Creation 2021

The goal of this code is to generate a dataset for each position (QB, RB, WR, TE, DST) containing the variables that will be used in tandem with 2019 data to build the regression models

Disclaimer: Variable names are inlclude 2020 instead of 2021. Please ignore this.

### Preprocessing

In [99]:
# Import Modules
import pandas as pd
import numpy as np
import math
import requests

# Set Display Options
pd.set_option('display.max_rows', 20)
pd.set_option('display.max_columns', None)

In [100]:
### Load Datasets

# Stats
StatsQB2020 = pd.read_csv("StatsQB2021.csv")
StatsRB2020 = pd.read_csv("StatsRB2021.csv")
StatsWR2020_Part1 = pd.read_csv("StatsWR2021_Part1.csv")
StatsWR2020_Part2 = pd.read_csv("StatsWR2021_Part2.csv")
StatsTE2020 = pd.read_csv("StatsTE2021.csv")

# Salaries
SalariesQB2020 = pd.read_csv("SalariesQB2021.csv")
SalariesRB2020_Part1 = pd.read_csv("SalariesRB2021_Part1.csv")
SalariesRB2020_Part2 = pd.read_csv("SalariesRB2021_Part2.csv")
SalariesRB2020_Part3 = pd.read_csv("SalariesRB2021_Part3.csv")
SalariesWR2020_Part1 = pd.read_csv("SalariesWR2021_Part1.csv")
SalariesWR2020_Part2 = pd.read_csv("SalariesWR2021_Part2.csv")
SalariesWR2020_Part3 = pd.read_csv("SalariesWR2021_Part3.csv")
SalariesTE2020_Part1 = pd.read_csv("SalariesTE2021_Part1.csv")
SalariesTE2020_Part2 = pd.read_csv("SalariesTE2021_Part2.csv")
SalariesTE2020_Part3 = pd.read_csv("SalariesTE2021_Part3.csv")

In [101]:
### Ensure that all datasets are under 2500 lines (FantasyData.com only allows users to download 2500 lines at a time)
print("StatsQB2020:",len(StatsQB2020))
print("StatsRB2020:",len(StatsRB2020))
print("StatsWR2020_Part1:",len(StatsWR2020_Part1))
print("StatsWR2020_Part2:",len(StatsWR2020_Part2))
print("StatsTE2020:",len(StatsTE2020))

print("SalariesQB2020:",len(SalariesQB2020))
print("SalariesRB2020_Part1:",len(SalariesRB2020_Part1))
print("SalariesRB2020_Part2:",len(SalariesRB2020_Part2))
print("SalariesRB2020_Part3:",len(SalariesRB2020_Part3))
print("SalariesWR2020_Part1:",len(SalariesWR2020_Part1))
print("SalariesWR2020_Part2:",len(SalariesWR2020_Part2))
print("SalariesWR2020_Part3:",len(SalariesWR2020_Part3))
print("SalariesTE2020_Part1:",len(SalariesTE2020_Part1))
print("SalariesTE2020_Part2:",len(SalariesTE2020_Part2))
print("SalariesTE2020_Part3:",len(SalariesTE2020_Part3))

StatsQB2020: 654
StatsRB2020: 1857
StatsWR2020_Part1: 1283
StatsWR2020_Part2: 1411
StatsTE2020: 1541
SalariesQB2020: 1751
SalariesRB2020_Part1: 1124
SalariesRB2020_Part2: 1069
SalariesRB2020_Part3: 982
SalariesWR2020_Part1: 1542
SalariesWR2020_Part2: 1654
SalariesWR2020_Part3: 1775
SalariesTE2020_Part1: 844
SalariesTE2020_Part2: 917
SalariesTE2020_Part3: 1013


In [102]:
### Combine Datasets that have parts
StatsWR2020 = StatsWR2020_Part1.append(StatsWR2020_Part2)
SalariesRB2020 = SalariesRB2020_Part1.append(SalariesRB2020_Part2).append(SalariesRB2020_Part3)
SalariesWR2020 = SalariesWR2020_Part1.append(SalariesWR2020_Part2).append(SalariesWR2020_Part3)
SalariesTE2020 = SalariesTE2020_Part1.append(SalariesTE2020_Part2).append(SalariesTE2020_Part3)

In [103]:
### Salaries: Ensure columns match for RB, WR, TE
print(SalariesRB2020.columns == SalariesWR2020.columns)
print(SalariesRB2020.columns == SalariesTE2020.columns) 

[ True  True  True  True  True  True  True  True  True  True  True]
[ True  True  True  True  True  True  True  True  True  True  True]


In [104]:
### Stats: Ensure columns match for RB, WR, TE
print(StatsRB2020.columns)
print(StatsWR2020.columns)
print(StatsTE2020.columns)
print(StatsWR2020.columns == StatsTE2020.columns)

for i in StatsWR2020.columns:
    if i not in StatsRB2020.columns:
        print(i) # can get rid of the uncommon columns for simplicity 
        
columns_list = ['Rank', 'PlayerID', 'Name', 'Team', 'Position', 'Week', 'Opponent',
                'RushingAttempts', 'RushingYards', 'RushingYardsPerAttempt','RushingTouchdowns',
                'ReceivingTargets', 'Receptions', 'ReceivingYards', 'ReceivingTouchdowns',
                'Fumbles', 'FumblesLost', 'FantasyPointsDraftKings']

StatsRB2020 = StatsRB2020[columns_list]
StatsWR2020 = StatsWR2020[columns_list]
StatsTE2020 = StatsTE2020[columns_list]

Index(['Rank', 'PlayerID', 'Name', 'Team', 'Position', 'Week', 'Opponent',
       'RushingAttempts', 'RushingYards', 'RushingYardsPerAttempt',
       'RushingTouchdowns', 'ReceivingTargets', 'Receptions', 'ReceivingYards',
       'ReceivingTouchdowns', 'Fumbles', 'FumblesLost',
       'FantasyPointsPerGameDraftKings', 'FantasyPointsDraftKings'],
      dtype='object')
Index(['Rank', 'PlayerID', 'Name', 'Team', 'Position', 'Week', 'Opponent',
       'ReceivingTargets', 'Receptions', 'ReceptionPercentage',
       'ReceivingYards', 'ReceivingTouchdowns', 'ReceivingLong',
       'ReceivingYardsPerTarget', 'ReceivingYardsPerReception',
       'RushingAttempts', 'RushingYards', 'RushingYardsPerAttempt',
       'RushingTouchdowns', 'Fumbles', 'FumblesLost',
       'FantasyPointsPerGameDraftKings', 'FantasyPointsDraftKings'],
      dtype='object')
Index(['Rank', 'PlayerID', 'Name', 'Team', 'Position', 'Week', 'Opponent',
       'ReceivingTargets', 'Receptions', 'ReceptionPercentage',
       'Re

In [105]:
### Create Flex DataFrame
StatsFLEX2020 = StatsRB2020.append(StatsWR2020).append(StatsTE2020)
SalariesFLEX2020 = SalariesRB2020.append(SalariesWR2020).append(SalariesTE2020)

### Creation of Shares Variables

Shares is a metric that we created inspired by Michael Salfino's market share report, a fantasy football writer for The Athletic. Shares are intended to encapsulate a player's usage/oppurtunities. We speculate that the higher a player's Shares are, the higher their fantasy points will be. The following Shares will be calculated for each position:

QBs:
- Pass Share: Passing attempts divided by total offensive plays 
- Rush Share: Rushing attempts divided by total running plays 

RBs, WRs, TEs:
- Rush Share: Rushing attempts divided by total running plays 
- Target Share: Intended targets divided by total passing plays 

In [106]:
### Add RushShare and TargetShare variables to RB, WR, TE, and FLEX Stats
def shares(df,df_flex):
    
    unique_player_ids = df.PlayerID.unique() # Initialize list of unqiue player ids

    frames = [] # Initialize frames list

    for i in unique_player_ids: # Loop through all unqiue player ids in df

        player_df = df[df.PlayerID == i] # Dataframe containing stats of player i
        
        rush_shares = [] # Initialize Rush Shares list
        target_shares = [] # Initialize Target Shares list

        for (w,t) in zip(player_df.Week,player_df.Team): # Loop through week and team of each row in player_df

            team_df = df_flex[(df_flex.Week == w)&(df_flex.Team == t)] # Dataframe containing stats of all RB, WR, TE druing week w for team t 
            
            rush_share = int(team_df[team_df.PlayerID == i].RushingAttempts)/int(team_df.RushingAttempts.sum()) # Rush Share: Rushing attempts divided by total running plays
            target_share = int(team_df[team_df.PlayerID == i].ReceivingTargets)/int(team_df.ReceivingTargets.sum()) # Target Share: Intended targets divided by total passing plays
            
            rush_shares.append(rush_share) # Append Rush Share to Rush Shares list
            target_shares.append(target_share) # Append Target Share to Target Shares list

        player_df['RushShare'] = rush_shares # Create RushShare as a column in player_df
        player_df['TargetShare'] = target_shares # Create TargetShare as a column in player_df

        frames.append(player_df) # Append player_df to frames list

    final_df = pd.concat(frames) # Combine all player_df in frames list
    df_final = final_df.sort_values(by=['Week','FantasyPointsDraftKings'], ascending=[True, False])
    return df_final

In [107]:
### Add PassShare and RushShare variables to QB Stats
def qb_shares(df,df_flex):

    unique_player_ids = df.PlayerID.unique() # Initialize list of unqiue player ids

    frames = [] # Initialize frames list

    for i in unique_player_ids: # Loop through all unqiue player ids in df

        player_df = df[df.PlayerID == i]  # Dataframe containing stats of player i

        pass_shares = [] # Initialize Pass Shares list
        rush_shares = [] # Initialize Rush Shares list

        for (w,t) in zip(player_df.Week,player_df.Team): # Loop through week and team of each row in player_df

            team_df = df_flex[(df_flex.Week == w)&(df_flex.Team == t)] # Dataframe containing stats of all RB, WR, TE druing week w for team t 
            
            passing_attempts = int(player_df[player_df.Week == w].PassingAttempts) # Define passing attempts 
            rushing_attempts = int(player_df[player_df.Week == w].RushingAttempts) # Define rushing attempts 

            pass_share = passing_attempts/(int(team_df.RushingAttempts.sum())+passing_attempts) # Pass Share: Passing attempts divided by total offensive plays
            rush_share = rushing_attempts/int(team_df.RushingAttempts.sum()) # Rush Share: Rushing attempts divided by total running plays

            pass_shares.append(pass_share) # Append Pass Share to Pass Shares list
            rush_shares.append(rush_share) # Append Rush Share to Rush Shares list

        player_df['PassShare'] = pass_shares # Create PassShare as a column in player_df
        player_df['RushShare'] = rush_shares # Create RushShare as a column in player_df
        
        frames.append(player_df) # Append player_df to frames list

    final_df = pd.concat(frames) # Combine all player_df in frames list
    df_final = final_df.sort_values(by=['Week','FantasyPointsDraftKings'], ascending=[True, False])
    return df_final

In [108]:
### Apply Shares functions
StatsQB2020 = qb_shares(StatsQB2020,StatsFLEX2020)
StatsRB2020 = shares(StatsRB2020,StatsFLEX2020)
StatsWR2020 = shares(StatsWR2020,StatsFLEX2020)
StatsTE2020 = shares(StatsTE2020,StatsFLEX2020)
StatsFLEX2020 = shares(StatsFLEX2020,StatsFLEX2020)

<ipython-input-107-6cfa398629a2>:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['PassShare'] = pass_shares # Create PassShare as a column in player_df
<ipython-input-107-6cfa398629a2>:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['RushShare'] = rush_shares # Create RushShare as a column in player_df
<ipython-input-107-6cfa398629a2>:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

<ipython-input-107-6cfa398629a2>:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['RushShare'] = rush_shares # Create RushShare as a column in player_df
<ipython-input-107-6cfa398629a2>:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['PassShare'] = pass_shares # Create PassShare as a column in player_df
<ipython-input-107-6cfa398629a2>:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

<ipython-input-107-6cfa398629a2>:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['PassShare'] = pass_shares # Create PassShare as a column in player_df
<ipython-input-107-6cfa398629a2>:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['RushShare'] = rush_shares # Create RushShare as a column in player_df
<ipython-input-107-6cfa398629a2>:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

<ipython-input-107-6cfa398629a2>:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['RushShare'] = rush_shares # Create RushShare as a column in player_df
<ipython-input-107-6cfa398629a2>:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['PassShare'] = pass_shares # Create PassShare as a column in player_df
<ipython-input-107-6cfa398629a2>:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

<ipython-input-107-6cfa398629a2>:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['PassShare'] = pass_shares # Create PassShare as a column in player_df
<ipython-input-107-6cfa398629a2>:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['RushShare'] = rush_shares # Create RushShare as a column in player_df
<ipython-input-107-6cfa398629a2>:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

...

<ipython-input-106-bd607b2bc1f7>:25: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['RushShare'] = rush_shares # Create RushShare as a column in player_df
<ipython-input-106-bd607b2bc1f7>:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['TargetShare'] = target_shares # Create TargetShare as a column in player_df
<ipython-input-106-bd607b2bc1f7>:25: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value i

<ipython-input-106-bd607b2bc1f7>:25: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['RushShare'] = rush_shares # Create RushShare as a column in player_df
<ipython-input-106-bd607b2bc1f7>:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['TargetShare'] = target_shares # Create TargetShare as a column in player_df
<ipython-input-106-bd607b2bc1f7>:25: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value i

<ipython-input-106-bd607b2bc1f7>:25: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['RushShare'] = rush_shares # Create RushShare as a column in player_df
<ipython-input-106-bd607b2bc1f7>:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['TargetShare'] = target_shares # Create TargetShare as a column in player_df
<ipython-input-106-bd607b2bc1f7>:25: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value i

<ipython-input-106-bd607b2bc1f7>:25: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['RushShare'] = rush_shares # Create RushShare as a column in player_df
<ipython-input-106-bd607b2bc1f7>:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['TargetShare'] = target_shares # Create TargetShare as a column in player_df
<ipython-input-106-bd607b2bc1f7>:25: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value i

<ipython-input-106-bd607b2bc1f7>:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['TargetShare'] = target_shares # Create TargetShare as a column in player_df
<ipython-input-106-bd607b2bc1f7>:25: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['RushShare'] = rush_shares # Create RushShare as a column in player_df
<ipython-input-106-bd607b2bc1f7>:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value i

In [109]:
### Merge DataFrames (RB, WR, FLEX)
selected_columns = ['PlayerID','Name_x','Position_x','Week','Team_x','Opponent_x','RushingAttempts','RushShare','ReceivingTargets','TargetShare','UpcomingOpponentPositionRank','DraftKingsSalary','FantasyPointsDraftKings_y','FantasyPointsDraftKings_x']
renamed_columns = ['PlayerID','Name','Position','Week','Team','Opponent','Attempts','RushShare','Targets','TargetShare','OPR','Salary','FantasyPoints','FantasyPoints_DraftKingsProjection']

WR2020 = pd.merge(SalariesWR2020, StatsWR2020, how="inner", left_on=["PlayerID", "Week"], right_on=["PlayerID", "Week"])
WR2020 = WR2020[selected_columns]
WR2020.columns = renamed_columns

RB2020 = pd.merge(SalariesRB2020, StatsRB2020, how="inner", left_on=["PlayerID", "Week"], right_on=["PlayerID", "Week"])
RB2020 = RB2020[selected_columns]
RB2020.columns = renamed_columns

TE2020 = pd.merge(SalariesTE2020, StatsTE2020, how="inner", left_on=["PlayerID", "Week"], right_on=["PlayerID", "Week"])
TE2020 = TE2020[selected_columns]
TE2020.columns = renamed_columns

FLEX2020 = pd.merge(SalariesFLEX2020, StatsFLEX2020, how="inner", left_on=["PlayerID", "Week"], right_on=["PlayerID", "Week"])
FLEX2020 = FLEX2020[selected_columns]
FLEX2020.columns = renamed_columns

In [110]:
### Merge DataFrames (QB)
selected_columns = ['PlayerID','Name_x','Position_x','Week','Team_x','Opponent_x','PassingAttempts','PassShare','RushingAttempts','RushShare','UpcomingOpponentPositionRank','DraftKingsSalary','FantasyPointsDraftKings_y','FantasyPointsDraftKings_x']
renamed_columns = ['PlayerID','Name','Position','Week','Team','Opponent','PassingAttempts','PassShare','RushingAttempts','RushShare','OPR','Salary','FantasyPoints','FantasyPoints_DraftKingsProjection']

QB2020 = pd.merge(SalariesQB2020, StatsQB2020, how="inner", left_on=["PlayerID", "Week"], right_on=["PlayerID", "Week"])
QB2020 = QB2020[selected_columns]
QB2020.columns = renamed_columns

In [111]:
QB2020

PlayerID             Name Position  Week Team Opponent  PassingAttempts  \
0       18890  Patrick Mahomes       QB     1   KC      CLE               36   
1       20889     Kyler Murray       QB     1  ARI      TEN               32   
2       19781    Lamar Jackson       QB     1  BAL       LV               30   
3       19801       Josh Allen       QB     1  BUF      PIT               51   
4       14536   Russell Wilson       QB     1  SEA      IND               23   
..        ...              ...      ...   ...  ...      ...              ...   
649     16763   Marcus Mariota       QB    17   LV      IND                1   
650     18018  Jacoby Brissett       QB    17  MIA      TEN                0   
651     18118    Brandon Allen       QB    17  CIN       KC                1   
652      8358      Brian Hoyer       QB    17   NE      JAX                4   
653     20055   Logan Woodside       QB    17  TEN      MIA                0   

     PassShare  RushingAttempts  RushShare  OPR  Salary  FantasyPoints  \
0     0.666667                5   0.277778   25  8100.0          36.28   
1     0.533333                5   0.178571   28  7600.0          34.56   
2     0.576923               12   0.545455   26  7700.0          20.00   
3     0.761194                9   0.562500    2  7400.0          18.20   
4     0.511111                5   0.227273   10  7000.0          27.06   
..         ...              ...        ...  ...     ...            ...   
649   0.040000                3   0.125000   23  5100.0           1.60   
650   0.000000                0   0.000000   22  5000.0           0.00   
651   0.071429                1   0.076923   27  5000.0           0.00   
652   0.111111                2   0.062500   20  4500.0           2.62   
653   0.000000                0   0.000000    8  4700.0           0.00   

     FantasyPoints_DraftKingsProjection  
0                                 27.40  
1                                 24.19  
2                                 23.93  
3                                 23.56  
4                                 22.20  
..                                  ...  
649                                0.28  
650                                0.19  
651                                0.11  
652                                0.08  
653                                0.05  

[654 rows x 14 columns]

In [112]:
RB2020

PlayerID                 Name Position  Week Team Opponent  Attempts  \
0        18877  Christian McCaffrey       RB     1  CAR      NYJ        21   
1        18872          Dalvin Cook       RB     1  MIN      CIN        20   
2        17959        Derrick Henry       RB     1  TEN      ARI        17   
3        18878         Alvin Kamara       RB     1   NO       GB        20   
4        19798           Nick Chubb       RB     1  CLE       KC        15   
...        ...                  ...      ...   ...  ...      ...       ...   
1852     20106            Ryan Nall       RB    17  CHI      NYG         0   
1853     12787         Nick Bellore       FB    17  SEA      DET         0   
1854     21126     Cullen Gillaspia       FB    17  NYG      CHI         0   
1855     20948         Sutton Smith       FB    17   LV      IND         0   
1856     19599         Trey Edmunds       RB    17  PIT      CLE         0   

      RushShare  Targets  TargetShare  OPR  Salary  FantasyPoints  \
0      0.954545        9     0.272727   16  9500.0           27.7   
1      0.909091        7     0.148936   25  9100.0           21.4   
2      0.850000        4     0.114286   17  8800.0           10.7   
3      0.645161        4     0.200000   27  8600.0           18.1   
4      0.625000        2     0.074074   23  7200.0           23.1   
...         ...      ...          ...  ...     ...            ...   
1852   0.000000        0     0.000000   25  4000.0            0.0   
1853   0.000000        0     0.000000   30  4000.0            0.0   
1854   0.000000        0     0.000000   21  4000.0            0.0   
1855   0.000000        0     0.000000    7  4000.0            0.0   
1856   0.000000        0     0.000000   11  4000.0            0.0   

      FantasyPoints_DraftKingsProjection  
0                                  23.75  
1                                  21.29  
2                                  21.53  
3                                  21.62  
4                                  15.59  
...                                  ...  
1852                                0.19  
1853                                0.16  
1854                                0.05  
1855                                0.00  
1856                                0.00  

[1857 rows x 14 columns]

In [113]:
WR2020

PlayerID             Name Position  Week Team Opponent  Attempts  \
0        18082      Tyreek Hill       WR     1   KC      CLE         1   
1        16470    Davante Adams       WR     1   GB       NO         0   
2        19802    Calvin Ridley       WR     1  ATL      PHI         0   
3        16906     Stefon Diggs       WR     1  BUF      PIT         0   
4        21042       A.J. Brown       WR     1  TEN      ARI         0   
...        ...              ...      ...   ...  ...      ...       ...   
2689     22615     Kawaan Baker       WR    17   NO      CAR         0   
2690     20376     Jordan Veasy       WR    17  HOU       SF         0   
2691     22311      Jeff Cotton       WR    17  JAX       NE         0   
2692     22327       J.J. Koski       WR    17  LAR      BAL         0   
2693     22973  Austin Trammell       WR    17  ATL      BUF         0   

      RushShare  Targets  TargetShare   OPR  Salary  FantasyPoints  \
0      0.055556       15     0.454545  26.0  8200.0           40.1   
1      0.000000        7     0.212121  16.0  8300.0           10.6   
2      0.000000        8     0.242424  25.0  7900.0           10.1   
3      0.000000       14     0.285714  15.0  7600.0           15.9   
4      0.000000        8     0.228571  11.0  7100.0           14.9   
...         ...      ...          ...   ...     ...            ...   
2689   0.000000        0     0.000000   6.0  3000.0            0.0   
2690   0.000000        0     0.000000  24.0  3000.0            0.0   
2691   0.000000        0     0.000000   5.0  3000.0            0.0   
2692   0.000000        0     0.000000  29.0  3000.0            0.0   
2693   0.000000        0     0.000000   1.0  3000.0            0.0   

      FantasyPoints_DraftKingsProjection  
0                                  21.14  
1                                  22.39  
2                                  19.26  
3                                  19.87  
4                                  18.12  
...                                  ...  
2689                                0.00  
2690                                0.00  
2691                                0.00  
2692                                0.00  
2693                                0.00  

[2694 rows x 14 columns]

In [114]:
TE2020 

PlayerID              Name Position  Week Team Opponent  Attempts  \
0        15048      Travis Kelce       TE     1   KC      CLE         0   
1        19063     George Kittle       TE     1   SF      DET         0   
2        16964     Darren Waller       TE     1   LV      BAL         0   
3        19803      Mark Andrews       TE     1  BAL       LV         0   
4        22508        Kyle Pitts       TE     1  ATL      PHI         0   
...        ...               ...      ...   ...  ...      ...       ...   
1537     21800   Mitchell Wilcox       TE    17  CIN       KC         0   
1538     23101      Parker Hesse       TE    17  ATL      BUF         0   
1539     21865  Stephen Sullivan       TE    17  CAR       NO         0   
1540     22663  Hunter Kampmoyer       TE    17  LAC      DEN         0   
1541     20199       David Wells       TE    17  ARI      DAL         0   

      RushShare  Targets  TargetShare  OPR  Salary  FantasyPoints  \
0           0.0        7     0.212121   28  8300.0           25.6   
1           0.0        5     0.217391   18  6300.0           11.8   
2           0.0       19     0.365385   10  7500.0           29.5   
3           0.0        5     0.172414   17  5300.0            5.0   
4           0.0        8     0.242424   22  4400.0            7.1   
...         ...      ...          ...  ...     ...            ...   
1537        0.0        0     0.000000   20  2500.0            0.0   
1538        0.0        3     0.142857    4  2500.0            6.1   
1539        0.0        0     0.000000    8  2500.0            0.0   
1540        0.0        0     0.000000    3  2500.0            0.0   
1541        0.0        0     0.000000   21  2500.0            0.0   

      FantasyPoints_DraftKingsProjection  
0                                  20.12  
1                                  16.67  
2                                  16.43  
3                                  13.78  
4                                  12.25  
...                                  ...  
1537                                0.07  
1538                                0.13  
1539                                0.00  
1540                                0.00  
1541                                0.00  

[1542 rows x 14 columns]

### Creation of Averages Variables

We now have players’ fantasy points, pass shares, rush shares, and target shares for each game. We will now transform these variables into lagged averages so that they can be used to predict fantasy points. We will create three types of lagged averages:

- Rolling: Rolling average of Metric X 
- Last 5: Average of the last 5 games of Metric X 
- Last 3: Average of the last 3 games of Metric X

where Metric X can be fantasy points, pass shares, rush shares, and target shares

In [115]:
### Function that computes averages for RB, WR, TE
def averages(df):

    unique_player_ids = df.PlayerID.unique() # Initialize list of unqiue player ids

    frames = []  # Initialize frames list

    for x in unique_player_ids: # Loop through all unqiue player ids in df

        player_df = df[df.PlayerID==x] # Dataframe containing stats of player i

        ####### ROLLING MEAN #######

        rush_share_mean = [np.nan] # Initialize Rush Share list with nan value as first element 
        target_share_mean = [np.nan] # Initialize Target Share list with nan value as first element 
        fantasy_points_mean = [np.nan] # Initialize Fantasy Points list with nan value as first element 

        for i in range(1,len(player_df)+1): # Loop through indices of player_df

            data_i = player_df.iloc[0:i] # Subset of player_df containing rows 0-i

            rush_share_mean.append(data_i.RushShare.mean()) # RushShareMean: Average of RushShare column in data_i
            target_share_mean.append(data_i.TargetShare.mean()) # TargetShareMean: Average of TargetShare column in data_i
            fantasy_points_mean.append(data_i.FantasyPoints.mean()) # FantasyPointsMean: Average of FantasyPoints column in data_i

        player_df['RushShareMean_Rolling'] = rush_share_mean[:-1] # Add RushShareMean_Rolling as a column in player_df
        player_df['TargetShareMean_Rolling'] = target_share_mean[:-1] # Add TargetShareMean_Rolling as a column in player_df
        player_df['FantasyPointsMean_Rolling'] = fantasy_points_mean[:-1] # Add FantasyPointsMean_Rolling as a column in player_df

        ####### LAST 3 GAMES MEAN #######

        if len(player_df) <= 3: # If player x has played three games or less, he has no averages of the last five games 

            rush_share_mean = [np.nan]*len(player_df)
            target_share_mean = [np.nan]*len(player_df)
            fantasy_points_mean = [np.nan]*len(player_df)

            player_df['RushShareMean_Last3'] = rush_share_mean
            player_df['TargetShareMean_Last3'] = target_share_mean
            player_df['FantasyPointsMean_Last3'] = fantasy_points_mean

        else: # If player x has played more than three games, averages of the last 3 games can be calculated  
            
            rush_share_mean = [np.nan]*3 # Initialize Rush Share list with nan value as first three elements 
            target_share_mean = [np.nan]*3 # Initialize Target Share list with nan value as first three elements
            fantasy_points_mean = [np.nan]*3 # Initialize Fantasy Points list with nan value as first three elements

            for i in range(len(player_df)-3): # Loop through indices of player_df minus last three rows

                data_i = player_df.iloc[0+i:3+i] # Subset of player_df containing three rows

                rush_share_mean.append(data_i.RushShare.mean()) # RushShareMean: Average of RushShare column in data_i
                target_share_mean.append(data_i.TargetShare.mean()) # TargetShareMean: Average of TargetShare column in data_i
                fantasy_points_mean.append(data_i.FantasyPoints.mean()) # FantasyPointsMean: Average of FantasyPoints column in data_i

            player_df['RushShareMean_Last3'] = rush_share_mean # Add RushShareMean_Last3 as a column in player_df
            player_df['TargetShareMean_Last3'] = target_share_mean # Add TargetShareMean_Last3 as a column in player_df
            player_df['FantasyPointsMean_Last3'] = fantasy_points_mean # Add FantasyPointsMean_Last3 as a column in player_df

        ####### LAST 5 GAMES MEAN #######

        if len(player_df) <= 5: # If player x has played five games or less, he has no averages of the last five games 

            rush_share_mean = [np.nan]*len(player_df)
            target_share_mean = [np.nan]*len(player_df)
            fantasy_points_mean = [np.nan]*len(player_df)

            player_df['RushShareMean_Last5'] = rush_share_mean
            player_df['TargetShareMean_Last5'] = target_share_mean
            player_df['FantasyPointsMean_Last5'] = fantasy_points_mean

        else:

            rush_share_mean = [np.nan]*5 # Initialize Rush Share list with nan value as first five elements 
            target_share_mean = [np.nan]*5 # Initialize Target Share list with nan value as first five elements 
            fantasy_points_mean = [np.nan]*5 # Initialize Fantasy Points list with nan value as first five elements 

            for i in range(len(player_df)-5): # Loop through indices of player_df minus last five rows

                data_i = player_df.iloc[0+i:5+i] # Subset of player_df containing five rows

                rush_share_mean.append(data_i.RushShare.mean()) # RushShareMean: Average of RushShare column in data_i
                target_share_mean.append(data_i.TargetShare.mean()) #  TargetShareMean: Average of TargetShare column in data_i
                fantasy_points_mean.append(data_i.FantasyPoints.mean()) # FantasyPointsMean: Average of FantasyPoints column in data_i

            player_df['RushShareMean_Last5'] = rush_share_mean # Add RushShareMean_Last5 as a column in player_df
            player_df['TargetShareMean_Last5'] = target_share_mean # Add RushShareMean_Last5 as a column in player_df
            player_df['FantasyPointsMean_Last5'] = fantasy_points_mean # Add FantasyPointsMean_Last5 as a column in player_df

        frames.append(player_df) # Append player_df to frames list

    final_df = pd.concat(frames) # Combine all player_df in frames list
    df_final = final_df.sort_values(by=['Week','FantasyPoints'], ascending=[True, False])
    return df_final

In [116]:
### Function that computes averages for QB
# Same format as previous function, but Target Share is replaced by Pass Share
def qb_averages(df):

    unique_player_ids = df.PlayerID.unique()

    frames = []

    for x in unique_player_ids:

        player_df = df[df.PlayerID==x]

        ####### ROLLING MEAN #######

        pass_share_mean = [np.nan]
        rush_share_mean = [np.nan]
        fantasy_points_mean = [np.nan]

        for i in range(1,len(player_df)+1):

            data_i = player_df.iloc[0:i]

            pass_share_mean.append(data_i.PassShare.mean())
            rush_share_mean.append(data_i.RushShare.mean())
            fantasy_points_mean.append(data_i.FantasyPoints.mean())

        player_df['PassShareMean_Rolling'] = pass_share_mean[:-1]
        player_df['RushShareMean_Rolling'] = rush_share_mean[:-1]
        player_df['FantasyPointsMean_Rolling'] = fantasy_points_mean[:-1]

        ####### LAST 3 GAMES MEAN #######

        if len(player_df) <= 3:

            pass_share_mean = [np.nan]*len(player_df)
            rush_share_mean = [np.nan]*len(player_df)
            fantasy_points_mean = [np.nan]*len(player_df)

            player_df['PassShareMean_Last3'] = pass_share_mean
            player_df['RushShareMean_Last3'] = rush_share_mean
            player_df['FantasyPointsMean_Last3'] = fantasy_points_mean

        else:

            pass_share_mean = [np.nan]*3
            rush_share_mean = [np.nan]*3
            fantasy_points_mean = [np.nan]*3

            for i in range(len(player_df)-3):

                data_i = player_df.iloc[0+i:3+i]

                pass_share_mean.append(data_i.PassShare.mean())
                rush_share_mean.append(data_i.RushShare.mean())
                fantasy_points_mean.append(data_i.FantasyPoints.mean())

            player_df['PassShareMean_Last3'] = pass_share_mean
            player_df['RushShareMean_Last3'] = rush_share_mean
            player_df['FantasyPointsMean_Last3'] = fantasy_points_mean

        ####### LAST 5 GAMES MEAN #######

        if len(player_df) <= 5:

            pass_share_mean = [np.nan]*len(player_df)
            rush_share_mean = [np.nan]*len(player_df)
            fantasy_points_mean = [np.nan]*len(player_df)

            player_df['PassShareMean_Last5'] = pass_share_mean
            player_df['RushShareMean_Last5'] = rush_share_mean
            player_df['FantasyPointsMean_Last5'] = fantasy_points_mean

        else:

            pass_share_mean = [np.nan]*5
            rush_share_mean = [np.nan]*5
            fantasy_points_mean = [np.nan]*5

            for i in range(len(player_df)-5):

                data_i = player_df.iloc[0+i:5+i]

                pass_share_mean.append(data_i.PassShare.mean())
                rush_share_mean.append(data_i.RushShare.mean())
                fantasy_points_mean.append(data_i.FantasyPoints.mean())

            player_df['PassShareMean_Last5'] = pass_share_mean
            player_df['RushShareMean_Last5'] = rush_share_mean
            player_df['FantasyPointsMean_Last5'] = fantasy_points_mean

        frames.append(player_df)

    final_df = pd.concat(frames)
    df_final = final_df.sort_values(by=['Week','FantasyPoints'], ascending=[True, False])
    return df_final

In [117]:
NewQB2020 = qb_averages(QB2020)
NewRB2020 = averages(RB2020)
NewWR2020 = averages(WR2020)
NewTE2020 = averages(TE2020)
NewFLEX2020 = averages(FLEX2020)

<ipython-input-116-61578924607a>:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['PassShareMean_Rolling'] = pass_share_mean[:-1]
<ipython-input-116-61578924607a>:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['RushShareMean_Rolling'] = rush_share_mean[:-1]
<ipython-input-116-61578924607a>:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https:

<ipython-input-116-61578924607a>:58: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['RushShareMean_Last3'] = rush_share_mean
<ipython-input-116-61578924607a>:59: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['FantasyPointsMean_Last3'] = fantasy_points_mean
<ipython-input-116-61578924607a>:87: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pand

<ipython-input-116-61578924607a>:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['RushShareMean_Rolling'] = rush_share_mean[:-1]
<ipython-input-116-61578924607a>:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['FantasyPointsMean_Rolling'] = fantasy_points_mean[:-1]
<ipython-input-116-61578924607a>:57: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation

<ipython-input-115-6e6f15c8cdc5>:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['RushShareMean_Rolling'] = rush_share_mean[:-1] # Add RushShareMean_Rolling as a column in player_df
<ipython-input-115-6e6f15c8cdc5>:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['TargetShareMean_Rolling'] = target_share_mean[:-1] # Add TargetShareMean_Rolling as a column in player_df
<ipython-input-115-6e6f15c8cdc5>:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a 

<ipython-input-115-6e6f15c8cdc5>:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['TargetShareMean_Rolling'] = target_share_mean[:-1] # Add TargetShareMean_Rolling as a column in player_df
<ipython-input-115-6e6f15c8cdc5>:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['FantasyPointsMean_Rolling'] = fantasy_points_mean[:-1] # Add FantasyPointsMean_Rolling as a column in player_df
<ipython-input-115-6e6f15c8cdc5>:56: SettingWithCopyWarning: 
A value is trying to be set on a copy of a s

...

<ipython-input-115-6e6f15c8cdc5>:86: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['RushShareMean_Last5'] = rush_share_mean # Add RushShareMean_Last5 as a column in player_df
<ipython-input-115-6e6f15c8cdc5>:87: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['TargetShareMean_Last5'] = target_share_mean # Add RushShareMean_Last5 as a column in player_df
<ipython-input-115-6e6f15c8cdc5>:88: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using

<ipython-input-115-6e6f15c8cdc5>:58: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['FantasyPointsMean_Last3'] = fantasy_points_mean # Add FantasyPointsMean_Last3 as a column in player_df
<ipython-input-115-6e6f15c8cdc5>:86: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['RushShareMean_Last5'] = rush_share_mean # Add RushShareMean_Last5 as a column in player_df
<ipython-input-115-6e6f15c8cdc5>:87: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
T

<ipython-input-115-6e6f15c8cdc5>:57: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['TargetShareMean_Last3'] = target_share_mean # Add TargetShareMean_Last3 as a column in player_df
<ipython-input-115-6e6f15c8cdc5>:58: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['FantasyPointsMean_Last3'] = fantasy_points_mean # Add FantasyPointsMean_Last3 as a column in player_df
<ipython-input-115-6e6f15c8cdc5>:86: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFr

<ipython-input-115-6e6f15c8cdc5>:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['TargetShareMean_Rolling'] = target_share_mean[:-1] # Add TargetShareMean_Rolling as a column in player_df
<ipython-input-115-6e6f15c8cdc5>:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['FantasyPointsMean_Rolling'] = fantasy_points_mean[:-1] # Add FantasyPointsMean_Rolling as a column in player_df
<ipython-input-115-6e6f15c8cdc5>:56: SettingWithCopyWarning: 
A value is trying to be set on a copy of a s

<ipython-input-115-6e6f15c8cdc5>:56: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['RushShareMean_Last3'] = rush_share_mean # Add RushShareMean_Last3 as a column in player_df
<ipython-input-115-6e6f15c8cdc5>:57: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  player_df['TargetShareMean_Last3'] = target_share_mean # Add TargetShareMean_Last3 as a column in player_df
<ipython-input-115-6e6f15c8cdc5>:58: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try usi

In [118]:
NewQB2020

PlayerID             Name Position  Week Team Opponent  PassingAttempts  \
0       18890  Patrick Mahomes       QB     1   KC      CLE               36   
1       20889     Kyler Murray       QB     1  ARI      TEN               32   
30      17922       Jared Goff       QB     1  DET       SF               57   
5        4314        Tom Brady       QB     1   TB      DAL               50   
8       18055     Dak Prescott       QB     1  DAL       TB               58   
..        ...              ...      ...   ...  ...      ...              ...   
650     18018  Jacoby Brissett       QB    17  MIA      TEN                0   
651     18118    Brandon Allen       QB    17  CIN       KC                1   
653     20055   Logan Woodside       QB    17  TEN      MIA                0   
648     20929     Brett Rypien       QB    17  DEN      LAC                2   
644     15201     Mike Glennon       QB    17  NYG      CHI               11   

     PassShare  RushingAttempts  RushShare  OPR  Salary  FantasyPoints  \
0     0.666667                5   0.277778   25  8100.0          36.28   
1     0.533333                5   0.178571   28  7600.0          34.56   
30    0.730769                3   0.142857    8  5100.0          32.92   
5     0.781250                0   0.000000   19  6700.0          32.16   
8     0.805556                4   0.285714   14  6200.0          31.42   
..         ...              ...        ...  ...     ...            ...   
650   0.000000                0   0.000000   22  5000.0           0.00   
651   0.071429                1   0.076923   27  5000.0           0.00   
653   0.000000                0   0.000000    8  4700.0           0.00   
648   0.076923                0   0.000000   18  4400.0           0.00   
644   0.220000                1   0.025641   29  5000.0          -1.74   

     FantasyPoints_DraftKingsProjection  PassShareMean_Rolling  \
0                                 27.40                    NaN   
1                                 24.19                    NaN   
30                                14.95                    NaN   
5                                 24.82                    NaN   
8                                 20.96                    NaN   
..                                  ...                    ...   
650                                0.19               0.419293   
651                                0.11               0.038105   
653                                0.05               0.000000   
648                                0.29                    NaN   
644                                8.44               0.585738   

     RushShareMean_Rolling  FantasyPointsMean_Rolling  PassShareMean_Last3  \
0                      NaN                        NaN                  NaN   
1                      NaN                        NaN                  NaN   
30                     NaN                        NaN                  NaN   
5                      NaN                        NaN                  NaN   
8                      NaN                        NaN                  NaN   
..                     ...                        ...                  ...   
650               0.107594                      7.932             0.186992   
651               0.046230                      1.030             0.039312   
653               0.055388                     -0.150             0.000000   
648                    NaN                        NaN                  NaN   
644               0.054877                      9.128             0.550608   

     RushShareMean_Last3  FantasyPointsMean_Last3  PassShareMean_Last5  \
0                    NaN                      NaN                  NaN   
1                    NaN                      NaN                  NaN   
30                   NaN                      NaN                  NaN   
5                    NaN                      NaN                  NaN   
8                    NaN                      NaN      

In [119]:
NewRB2020

PlayerID                 Name Position  Week Team Opponent  Attempts  \
6        18858            Joe Mixon       RB     1  CIN      MIN        29   
0        18877  Christian McCaffrey       RB     1  CAR      NYJ        21   
34       18995      Jamaal Williams       RB     1  DET       SF         9   
22       21684        D'Andre Swift       RB     1  DET       SF        11   
26       16776    Melvin Gordon III       RB     1  DEN      NYG        11   
...        ...                  ...      ...   ...  ...      ...       ...   
1811     22441      Nathan Cottrell       RB    17  JAX       NE         0   
1856     19599         Trey Edmunds       RB    17  PIT      CLE         0   
1848     15185        Kenjon Barner       RB    17   TB      NYJ         0   
1831     21825        Spencer Brown       RB    17  CAR       NO         0   
1803     21774       Tony Jones Jr.       RB    17   NO      CAR         1   

      RushShare  Targets  TargetShare  OPR  Salary  FantasyPoints  \
6      0.828571        4     0.153846   28  6200.0           28.0   
0      0.954545        9     0.272727   16  9500.0           27.7   
34     0.428571        9     0.160714    7  4500.0           25.0   
22     0.523810       11     0.196429    7  6900.0           24.4   
26     0.440000        3     0.085714   19  5300.0           23.8   
...         ...      ...          ...  ...     ...            ...   
1811   0.000000        0     0.000000   18  4700.0            0.0   
1856   0.000000        0     0.000000   11  4000.0            0.0   
1848   0.000000        0     0.000000   32  4000.0            0.0   
1831   0.000000        0     0.000000    2  4000.0            0.0   
1803   0.062500        0     0.000000   12  4000.0           -0.2   

      FantasyPoints_DraftKingsProjection  RushShareMean_Rolling  \
6                                  16.78                    NaN   
0                                  23.75                    NaN   
34                                  8.93                    NaN   
22                                 14.00                    NaN   
26                                 11.36                    NaN   
...                                  ...                    ...   
1811                                2.10               0.020833   
1856                                0.00               0.000000   
1848                                0.16               0.000000   
1831                                0.49                    NaN   
1803                                2.88               0.214324   

      TargetShareMean_Rolling  FantasyPointsMean_Rolling  RushShareMean_Last3  \
6                         NaN                        NaN                  NaN   
0                         NaN                        NaN                  NaN   
34                        NaN                        NaN                  NaN   
22                        NaN                        NaN                  NaN   
26                        NaN                        NaN                  NaN   
...                       ...                        ...                  ...   
1811                 0.000000                   0.150000                  NaN   
1856                 0.000000                   0.000000                  NaN   
1848                 0.000000                   0.000000                  NaN   
1831                      NaN                        NaN                  NaN   
1803                 0.035847                   2.233333             0.093939   

      TargetShareMean_Last3  FantasyPointsMean_Last3  RushShareMean_Last5  \
6                       NaN                      NaN                  NaN   
0                       NaN                      NaN                  NaN   
34                      NaN                      NaN                  NaN   
22                      NaN                      NaN                  NaN   
26                      NaN                      NaN                  NaN   


In [120]:
NewWR2020

PlayerID             Name Position  Week Team Opponent  Attempts  \
19       16765     Amari Cooper       WR     1  DAL       TB         0   
0        18082      Tyreek Hill       WR     1   KC      CLE         1   
26       20932     Deebo Samuel       WR     1   SF      DET         0   
11       15534     Adam Thielen       WR     1  MIN      CIN         0   
13       16830    Tyler Lockett       WR     1  SEA      IND         0   
...        ...              ...      ...   ...  ...      ...       ...   
2691     22311      Jeff Cotton       WR    17  JAX       NE         0   
2693     22973  Austin Trammell       WR    17  ATL      BUF         0   
2597     21686     Jalen Reagor       WR    17  PHI      WAS         1   
2650     16855    Ty Montgomery       WR    17   NO      CAR         1   
2609     20722  Diontae Spencer       WR    17  DEN      LAC         0   

      RushShare  Targets  TargetShare   OPR  Salary  FantasyPoints  \
19     0.000000       16     0.280702  19.0  6000.0           41.9   
0      0.055556       15     0.454545  26.0  8200.0           40.1   
26     0.000000       12     0.521739  30.0  5900.0           35.9   
11     0.000000       10     0.212766  17.0  7000.0           30.2   
13     0.000000        5     0.238095  18.0  6700.0           29.0   
...         ...      ...          ...   ...     ...            ...   
2691   0.000000        0     0.000000   5.0  3000.0            0.0   
2693   0.000000        0     0.000000   1.0  3000.0            0.0   
2597   0.037037        1     0.040000  30.0  3300.0           -0.3   
2650   0.062500        0     0.000000   6.0  3100.0           -0.4   
2609   0.000000        0     0.000000   4.0  3000.0           -1.0   

      FantasyPoints_DraftKingsProjection  RushShareMean_Rolling  \
19                                 15.25                    NaN   
0                                  21.14                    NaN   
26                                 14.00                    NaN   
11                                 15.48                    NaN   
13                                 15.97                    NaN   
...                                  ...                    ...   
2691                                0.00                    NaN   
2693                                0.00                    NaN   
2597                                6.12               0.017354   
2650                                2.15               0.058253   
2609                                5.56               0.000000   

      TargetShareMean_Rolling  FantasyPointsMean_Rolling  RushShareMean_Last3  \
19                        NaN                        NaN                  NaN   
0                         NaN                        NaN                  NaN   
26                        NaN                        NaN                  NaN   
11                        NaN                        NaN                  NaN   
13                        NaN                        NaN                  NaN   
...                       ...                        ...                  ...   
2691                      NaN                        NaN                  NaN   
2693                      NaN                        NaN                  NaN   
2597                 0.128929                   4.900000             0.009009   
2650                 0.067645                   2.433333             0.088889   
2609                 0.009805                  -0.021429             0.000000   

      TargetShareMean_Last3  FantasyPointsMean_Last3  RushShareMean_Last5  \
19                      NaN                      NaN                  NaN   
0                       NaN                      NaN                  NaN   
26                      NaN                      NaN                  NaN   
11                      NaN                      NaN                  NaN   
13                      NaN                      NaN                  NaN   
...                     ...         

In [121]:
NewTE2020

PlayerID              Name Position  Week Team Opponent  Attempts  \
2        16964     Darren Waller       TE     1   LV      BAL         0   
13       10974    Rob Gronkowski       TE     1   TB      DAL         0   
5        20805    T.J. Hockenson       TE     1  DET       SF         0   
0        15048      Travis Kelce       TE     1   KC      CLE         0   
32       21738     Juwan Johnson       TE     1   NO       GB         0   
...        ...               ...      ...   ...  ...      ...       ...   
1527     20134       Kevin Rader       TE    17  PIT      CLE         0   
1541     20199       David Wells       TE    17  ARI      DAL         0   
1539     21865  Stephen Sullivan       TE    17  CAR       NO         0   
1489     21676     Jared Pinkney       TE    17  DET      SEA         0   
1540     22663  Hunter Kampmoyer       TE    17  LAC      DEN         0   

      RushShare  Targets  TargetShare  OPR  Salary  FantasyPoints  \
2           0.0       19     0.365385   10  7500.0           29.5   
13          0.0        8     0.173913   16  3900.0           29.0   
5           0.0       10     0.178571    1  4900.0           25.7   
0           0.0        7     0.212121   28  8300.0           25.6   
32          0.0        3     0.150000    4  3000.0           17.1   
...         ...      ...          ...  ...     ...            ...   
1527        0.0        0     0.000000   22  2500.0            0.0   
1541        0.0        0     0.000000   21  2500.0            0.0   
1539        0.0        0     0.000000    8  2500.0            0.0   
1489        0.0        0     0.000000   28  2500.0            0.0   
1540        0.0        0     0.000000    3  2500.0            0.0   

      FantasyPoints_DraftKingsProjection  RushShareMean_Rolling  \
2                                  16.43                    NaN   
13                                  8.79                    NaN   
5                                  12.61                    NaN   
0                                  20.12                    NaN   
32                                  5.80                    NaN   
...                                  ...                    ...   
1527                                0.65                    0.0   
1541                                0.00                    0.0   
1539                                0.00                    0.0   
1489                                4.00                    NaN   
1540                                0.00                    NaN   

      TargetShareMean_Rolling  FantasyPointsMean_Rolling  RushShareMean_Last3  \
2                         NaN                        NaN                  NaN   
13                        NaN                        NaN                  NaN   
5                         NaN                        NaN                  NaN   
0                         NaN                        NaN                  NaN   
32                        NaN                        NaN                  NaN   
...                       ...                        ...                  ...   
1527                 0.021164                        0.7                  0.0   
1541                 0.000000                        0.0                  NaN   
1539                 0.023256                        0.0                  NaN   
1489                      NaN                        NaN                  NaN   
1540                      NaN                        NaN                  NaN   

      TargetShareMean_Last3  FantasyPointsMean_Last3  RushShareMean_Last5  \
2                       NaN                      NaN                  NaN   
13                      NaN                      NaN                  NaN   
5                       NaN                      NaN                  NaN   
0                       NaN                      NaN                  NaN   
32                      NaN                      NaN                  NaN   
...                     ...         

In [122]:
NewFLEX2020

PlayerID              Name Position  Week Team Opponent  Attempts  \
1876     16765      Amari Cooper       WR     1  DAL       TB         0   
1857     18082       Tyreek Hill       WR     1   KC      CLE         1   
1883     20932      Deebo Samuel       WR     1   SF      DET         0   
1868     15534      Adam Thielen       WR     1  MIN      CIN         0   
4553     16964     Darren Waller       TE     1   LV      BAL         0   
...        ...               ...      ...   ...  ...      ...       ...   
6091     22663  Hunter Kampmoyer       TE    17  LAC      DEN         0   
1803     21774    Tony Jones Jr.       RB    17   NO      CAR         1   
4454     21686      Jalen Reagor       WR    17  PHI      WAS         1   
4507     16855     Ty Montgomery       WR    17   NO      CAR         1   
4466     20722   Diontae Spencer       WR    17  DEN      LAC         0   

      RushShare  Targets  TargetShare   OPR  Salary  FantasyPoints  \
1876   0.000000       16     0.280702  19.0  6000.0           41.9   
1857   0.055556       15     0.454545  26.0  8200.0           40.1   
1883   0.000000       12     0.521739  30.0  5900.0           35.9   
1868   0.000000       10     0.212766  17.0  7000.0           30.2   
4553   0.000000       19     0.365385  10.0  7500.0           29.5   
...         ...      ...          ...   ...     ...            ...   
6091   0.000000        0     0.000000   3.0  2500.0            0.0   
1803   0.062500        0     0.000000  12.0  4000.0           -0.2   
4454   0.037037        1     0.040000  30.0  3300.0           -0.3   
4507   0.062500        0     0.000000   6.0  3100.0           -0.4   
4466   0.000000        0     0.000000   4.0  3000.0           -1.0   

      FantasyPoints_DraftKingsProjection  RushShareMean_Rolling  \
1876                               15.25                    NaN   
1857                               21.14                    NaN   
1883                               14.00                    NaN   
1868                               15.48                    NaN   
4553                               16.43                    NaN   
...                                  ...                    ...   
6091                                0.00                    NaN   
1803                                2.88               0.214324   
4454                                6.12               0.017354   
4507                                2.15               0.058253   
4466                                5.56               0.000000   

      TargetShareMean_Rolling  FantasyPointsMean_Rolling  RushShareMean_Last3  \
1876                      NaN                        NaN                  NaN   
1857                      NaN                        NaN                  NaN   
1883                      NaN                        NaN                  NaN   
1868                      NaN                        NaN                  NaN   
4553                      NaN                        NaN                  NaN   
...                       ...                        ...                  ...   
6091                      NaN                        NaN                  NaN   
1803                 0.035847                   2.233333             0.093939   
4454                 0.128929                   4.900000             0.009009   
4507                 0.067645                   2.433333             0.088889   
4466                 0.009805                  -0.021429             0.000000   

      TargetShareMean_Last3  FantasyPointsMean_Last3  RushShareMean_Last5  \
1876                    NaN                      NaN                  NaN   
1857                    NaN                      NaN                  NaN   
1883                    NaN                      NaN                  NaN   
1868                    NaN                      NaN                  NaN   
4553                    NaN                      NaN                  NaN   
...                     

### Injuries 

Injuries of a player’s teammates play an integral role in their fantasy point production. Therefore, we will create for injury variables:

- QB Injured: Whether the starting quarterback on player X’s team is injured  
- RB Injured: Amount of fantasy-relevant running backs that are injured on on player X’s 
- WR Injured: Amount of fantasy-relevant wide receivers that are injured on on player X’s
- TE Injured: Whether the starting tight end on player X’s team is injured  

Where player X is the player of focus and fantasy-relevant players are those whose rolling mean of canasta points is above their team’s average 

In [123]:
### Load Injury Data through SportsData.io API
season = '2021REG'
weeks = ['1','2','3','4','5','6','7','8','9','10','11','12','13','14','5','16','17']
injuries_list = []
for week in weeks:
    url = 'https://api.sportsdata.io/v3/nfl/stats/json/Injuries/'+season+'/'+week
    api_key = '5d1dd6725ca045d98899713256aadd2e'
    headers = {'Ocp-Apim-Subscription-Key': '{key}'.format(key=api_key)}
    injuries_raw = json.loads(requests.get(url, headers=headers).text)
    injuries_df = pd.DataFrame(injuries_raw)
    injuries_list.append(injuries_df)
injuries = pd.concat(injuries_list)

InjuriesQB2020 = injuries[(injuries.Position == 'QB')&(injuries.DeclaredInactive == True)]
InjuriesRB2020 = injuries[((injuries.Position == 'RB')|(injuries.Position == 'FB'))&(injuries.DeclaredInactive == True)]
InjuriesWR2020 = injuries[(injuries.Position == 'WR')&(injuries.DeclaredInactive == True)]
InjuriesTE2020 = injuries[(injuries.Position == 'TE')&(injuries.DeclaredInactive == True)]
InjuriesFLEX2020 = InjuriesRB2020.append(InjuriesWR2020).append(InjuriesTE2020)
Injuries2020 = InjuriesQB2020.append(InjuriesFLEX2020)

In [124]:
Injuries2020

InjuryID  SeasonType  Season  Week  PlayerID             Name Position  \
10     275145           1    2021     1     16116      AJ McCarron       QB   
85     275462           1    2021     1     20283        Tim Boyle       QB   
104    275449           1    2021     1     21815     Sam Ehlinger       QB   
136    275990           1    2021     1     19029  Nathan Peterman       QB   
169    274289           1    2021     1     20954  Jarrett Stidham       QB   
..        ...         ...     ...   ...       ...              ...      ...   
437    287120           1    2021    17     16451       Eric Ebron       TE   
507    287605           1    2021    17     22418     Tommy Hudson       TE   
511    287626           1    2021    17     22660     Briley Moore       TE   
525    287127           1    2021    17     16656     Logan Thomas       TE   
532    287364           1    2021    17     19982   Dylan Cantrell       TE   

     Number Team Opponent   BodyPart     Status   Practice  \
10        5  ATL      PHI  Scrambled  Scrambled  Scrambled   
85       12  DET       SF  Scrambled  Scrambled  Scrambled   
104       4  IND      SEA  Scrambled  Scrambled  Scrambled   
136       3   LV      BAL  Scrambled  Scrambled  Scrambled   
169       4   NE      MIA  Scrambled  Scrambled  Scrambled   
..      ...  ...      ...        ...        ...        ...   
437      85  PIT      CLE  Scrambled  Scrambled  Scrambled   
507      89  TEN      MIA  Scrambled  Scrambled  Scrambled   
511      49  TEN      MIA  Scrambled  Scrambled  Scrambled   
525      82  WAS      PHI  Scrambled  Scrambled  Scrambled   
532      45  WAS      PHI  Scrambled  Scrambled  Scrambled   

    PracticeDescription              Updated  DeclaredInactive  TeamID  \
10            Scrambled  2021-09-12T12:57:33              True       2   
85            Scrambled  2021-09-12T12:57:33              True      11   
104           Scrambled  2021-09-12T12:57:33              True      14   
136           Scrambled  2021-09-13T20:12:30              True      25   
169           Scrambled  2021-09-12T16:22:31              True      21   
..                  ...                  ...               ...     ...   
437           Scrambled  2022-01-03T20:12:33              True      28   
507           Scrambled  2022-01-02T12:57:31              True      34   
511           Scrambled  2022-01-02T12:57:31              True      34   
525           Scrambled  2022-01-02T12:57:31              True      35   
532           Scrambled  2022-01-02T12:57:31              True      35   

     OpponentID  
10         26.0  
85         31.0  
104        30.0  
136         3.0  
169        19.0  
..          ...  
437         8.0  
507        19.0  
511        19.0  
525        26.0  
532        26.0  

[2031 rows x 18 columns]

In [125]:
def injuries(df):
    
    QBInjuries = [] # Initialize QB Injuries list
    RBInjuries = [] # Initialize RB Injuries list
    WRInjuries = [] # Initialize WR Injuries list
    TEInjuries = [] # Initialize TE Injuries list

    for i in range(len(df)): # Loop through all possible 

        row_active = df.iloc[i,] # player i in df

        injury_df = Injuries2020[(Injuries2020.Team == row_active.Team)&(Injuries2020.Week == row_active.Week)] #  Players that are injured on the same team and week as player i

        QBInjured = 0 # Initialize whether starting QB is injured 
        RBInjured = 0 # Initialize amount of RBs injured
        WRInjured = 0 # Initialize amount of WRs injured
        TEInjured = 0 # Initialize whether starting TE is injured 

        for row_injured in range(len(injury_df)):

            name = injury_df.Name.iloc[row_injured,] #
            week = injury_df.Week.iloc[row_injured,]
            position = injury_df.Position.iloc[row_injured,]
            team = injury_df.Team.iloc[row_injured,]

            if position == 'QB':
                int_df = NewQB2020[(NewQB2020.Team == team)&(NewQB2020.Week < week)].reset_index()
                if len(int_df) != 0:
                    a_fpms = []
                    for j in int_df.Name.unique():
                        qb_j = int_df[int_df.Name == j]
                        most_recent = qb_j.iloc[len(qb_j)-1,]
                        a_fpm = most_recent.FantasyPointsMean_Rolling
                        if math.isnan(a_fpm) == True:
                            a_fpm = 0
                        a_fpms.append(a_fpm)
                    index = a_fpms.index(max(a_fpms))
                    if int_df.Name.unique()[index] == name:
                        QBInjured += 1

            elif position == 'RB':
                int_df = NewRB2020[(NewRB2020.Name == name)&(NewRB2020.Week < week)].reset_index()
                if len(int_df) != 0:
                    most_recent = int_df.iloc[len(int_df)-1,]
                    i_fpm = most_recent.FantasyPointsMean_Rolling
                    flexes = NewFLEX2020[(NewFLEX2020.Team == team)&(NewFLEX2020.Week < week)]
                    relevant_flexes = flexes[flexes.FantasyPointsMean_Rolling > 0]
                    avg_fpm = relevant_flexes.FantasyPointsMean_Rolling.mean()
                    if i_fpm >= avg_fpm:
                        RBInjured += 1

            elif position == 'WR':
                int_df = NewWR2020[(NewWR2020.Name == name)&(NewWR2020.Week < week)].reset_index()
                if len(int_df) != 0:
                    most_recent = int_df.iloc[len(int_df)-1,]
                    i_fpm = most_recent.FantasyPointsMean_Rolling
                    flexes = NewFLEX2020[(NewFLEX2020.Team == team)&(NewFLEX2020.Week < week)]
                    relevant_flexes = flexes[flexes.FantasyPointsMean_Rolling > 0]
                    avg_fpm = relevant_flexes.FantasyPointsMean_Rolling.mean()
                    if i_fpm >= avg_fpm:
                        WRInjured += 1

            elif position == 'TE':
                int_df = NewTE2020[(NewTE2020.Team == team)&(NewTE2020.Week < week)].reset_index()
                if len(int_df) != 0:
                    a_fpms = []
                    for j in int_df.Name.unique():
                        te_j = int_df[int_df.Name == j]
                        most_recent = te_j.iloc[len(te_j)-1,]
                        a_fpm = most_recent.FantasyPointsMean_Rolling
                        if math.isnan(a_fpm) == True:
                            a_fpm = 0
                        a_fpms.append(a_fpm)
                    index = a_fpms.index(max(a_fpms))
                    if int_df.Name.unique()[index] == name:
                        TEInjured += 1

        QBInjuries.append(QBInjured)
        RBInjuries.append(RBInjured)
        WRInjuries.append(WRInjured)
        TEInjuries.append(TEInjured)

    df['QBInjured'] = QBInjuries
    df['RBInjured'] = RBInjuries
    df['WRInjured'] = WRInjuries
    df['TEInjured'] = TEInjuries
    return df

In [126]:
NewNewQB2020 = injuries(NewQB2020)
NewNewRB2020 = injuries(NewRB2020)
NewNewWR2020 = injuries(NewWR2020)
NewNewTE2020 = injuries(NewTE2020)

In [127]:
NewNewQB2020

PlayerID             Name Position  Week Team Opponent  PassingAttempts  \
0       18890  Patrick Mahomes       QB     1   KC      CLE               36   
1       20889     Kyler Murray       QB     1  ARI      TEN               32   
30      17922       Jared Goff       QB     1  DET       SF               57   
5        4314        Tom Brady       QB     1   TB      DAL               50   
8       18055     Dak Prescott       QB     1  DAL       TB               58   
..        ...              ...      ...   ...  ...      ...              ...   
650     18018  Jacoby Brissett       QB    17  MIA      TEN                0   
651     18118    Brandon Allen       QB    17  CIN       KC                1   
653     20055   Logan Woodside       QB    17  TEN      MIA                0   
648     20929     Brett Rypien       QB    17  DEN      LAC                2   
644     15201     Mike Glennon       QB    17  NYG      CHI               11   

     PassShare  RushingAttempts  RushShare  OPR  Salary  FantasyPoints  \
0     0.666667                5   0.277778   25  8100.0          36.28   
1     0.533333                5   0.178571   28  7600.0          34.56   
30    0.730769                3   0.142857    8  5100.0          32.92   
5     0.781250                0   0.000000   19  6700.0          32.16   
8     0.805556                4   0.285714   14  6200.0          31.42   
..         ...              ...        ...  ...     ...            ...   
650   0.000000                0   0.000000   22  5000.0           0.00   
651   0.071429                1   0.076923   27  5000.0           0.00   
653   0.000000                0   0.000000    8  4700.0           0.00   
648   0.076923                0   0.000000   18  4400.0           0.00   
644   0.220000                1   0.025641   29  5000.0          -1.74   

     FantasyPoints_DraftKingsProjection  PassShareMean_Rolling  \
0                                 27.40                    NaN   
1                                 24.19                    NaN   
30                                14.95                    NaN   
5                                 24.82                    NaN   
8                                 20.96                    NaN   
..                                  ...                    ...   
650                                0.19               0.419293   
651                                0.11               0.038105   
653                                0.05               0.000000   
648                                0.29                    NaN   
644                                8.44               0.585738   

     RushShareMean_Rolling  FantasyPointsMean_Rolling  PassShareMean_Last3  \
0                      NaN                        NaN                  NaN   
1                      NaN                        NaN                  NaN   
30                     NaN                        NaN                  NaN   
5                      NaN                        NaN                  NaN   
8                      NaN                        NaN                  NaN   
..                     ...                        ...                  ...   
650               0.107594                      7.932             0.186992   
651               0.046230                      1.030             0.039312   
653               0.055388                     -0.150             0.000000   
648                    NaN                        NaN                  NaN   
644               0.054877                      9.128             0.550608   

     RushShareMean_Last3  FantasyPointsMean_Last3  PassShareMean_Last5  \
0                    NaN                      NaN                  NaN   
1                    NaN                      NaN                  NaN   
30                   NaN                      NaN                  NaN   
5                    NaN                      NaN                  NaN   
8                    NaN                      NaN      

In [128]:
NewNewRB2020

PlayerID                 Name Position  Week Team Opponent  Attempts  \
6        18858            Joe Mixon       RB     1  CIN      MIN        29   
0        18877  Christian McCaffrey       RB     1  CAR      NYJ        21   
34       18995      Jamaal Williams       RB     1  DET       SF         9   
22       21684        D'Andre Swift       RB     1  DET       SF        11   
26       16776    Melvin Gordon III       RB     1  DEN      NYG        11   
...        ...                  ...      ...   ...  ...      ...       ...   
1811     22441      Nathan Cottrell       RB    17  JAX       NE         0   
1856     19599         Trey Edmunds       RB    17  PIT      CLE         0   
1848     15185        Kenjon Barner       RB    17   TB      NYJ         0   
1831     21825        Spencer Brown       RB    17  CAR       NO         0   
1803     21774       Tony Jones Jr.       RB    17   NO      CAR         1   

      RushShare  Targets  TargetShare  OPR  Salary  FantasyPoints  \
6      0.828571        4     0.153846   28  6200.0           28.0   
0      0.954545        9     0.272727   16  9500.0           27.7   
34     0.428571        9     0.160714    7  4500.0           25.0   
22     0.523810       11     0.196429    7  6900.0           24.4   
26     0.440000        3     0.085714   19  5300.0           23.8   
...         ...      ...          ...  ...     ...            ...   
1811   0.000000        0     0.000000   18  4700.0            0.0   
1856   0.000000        0     0.000000   11  4000.0            0.0   
1848   0.000000        0     0.000000   32  4000.0            0.0   
1831   0.000000        0     0.000000    2  4000.0            0.0   
1803   0.062500        0     0.000000   12  4000.0           -0.2   

      FantasyPoints_DraftKingsProjection  RushShareMean_Rolling  \
6                                  16.78                    NaN   
0                                  23.75                    NaN   
34                                  8.93                    NaN   
22                                 14.00                    NaN   
26                                 11.36                    NaN   
...                                  ...                    ...   
1811                                2.10               0.020833   
1856                                0.00               0.000000   
1848                                0.16               0.000000   
1831                                0.49                    NaN   
1803                                2.88               0.214324   

      TargetShareMean_Rolling  FantasyPointsMean_Rolling  RushShareMean_Last3  \
6                         NaN                        NaN                  NaN   
0                         NaN                        NaN                  NaN   
34                        NaN                        NaN                  NaN   
22                        NaN                        NaN                  NaN   
26                        NaN                        NaN                  NaN   
...                       ...                        ...                  ...   
1811                 0.000000                   0.150000                  NaN   
1856                 0.000000                   0.000000                  NaN   
1848                 0.000000                   0.000000                  NaN   
1831                      NaN                        NaN                  NaN   
1803                 0.035847                   2.233333             0.093939   

      TargetShareMean_Last3  FantasyPointsMean_Last3  RushShareMean_Last5  \
6                       NaN                      NaN                  NaN   
0                       NaN                      NaN                  NaN   
34                      NaN                      NaN                  NaN   
22                      NaN                      NaN                  NaN   
26                      NaN                      NaN                  NaN   


In [129]:
NewNewWR2020

PlayerID             Name Position  Week Team Opponent  Attempts  \
19       16765     Amari Cooper       WR     1  DAL       TB         0   
0        18082      Tyreek Hill       WR     1   KC      CLE         1   
26       20932     Deebo Samuel       WR     1   SF      DET         0   
11       15534     Adam Thielen       WR     1  MIN      CIN         0   
13       16830    Tyler Lockett       WR     1  SEA      IND         0   
...        ...              ...      ...   ...  ...      ...       ...   
2691     22311      Jeff Cotton       WR    17  JAX       NE         0   
2693     22973  Austin Trammell       WR    17  ATL      BUF         0   
2597     21686     Jalen Reagor       WR    17  PHI      WAS         1   
2650     16855    Ty Montgomery       WR    17   NO      CAR         1   
2609     20722  Diontae Spencer       WR    17  DEN      LAC         0   

      RushShare  Targets  TargetShare   OPR  Salary  FantasyPoints  \
19     0.000000       16     0.280702  19.0  6000.0           41.9   
0      0.055556       15     0.454545  26.0  8200.0           40.1   
26     0.000000       12     0.521739  30.0  5900.0           35.9   
11     0.000000       10     0.212766  17.0  7000.0           30.2   
13     0.000000        5     0.238095  18.0  6700.0           29.0   
...         ...      ...          ...   ...     ...            ...   
2691   0.000000        0     0.000000   5.0  3000.0            0.0   
2693   0.000000        0     0.000000   1.0  3000.0            0.0   
2597   0.037037        1     0.040000  30.0  3300.0           -0.3   
2650   0.062500        0     0.000000   6.0  3100.0           -0.4   
2609   0.000000        0     0.000000   4.0  3000.0           -1.0   

      FantasyPoints_DraftKingsProjection  RushShareMean_Rolling  \
19                                 15.25                    NaN   
0                                  21.14                    NaN   
26                                 14.00                    NaN   
11                                 15.48                    NaN   
13                                 15.97                    NaN   
...                                  ...                    ...   
2691                                0.00                    NaN   
2693                                0.00                    NaN   
2597                                6.12               0.017354   
2650                                2.15               0.058253   
2609                                5.56               0.000000   

      TargetShareMean_Rolling  FantasyPointsMean_Rolling  RushShareMean_Last3  \
19                        NaN                        NaN                  NaN   
0                         NaN                        NaN                  NaN   
26                        NaN                        NaN                  NaN   
11                        NaN                        NaN                  NaN   
13                        NaN                        NaN                  NaN   
...                       ...                        ...                  ...   
2691                      NaN                        NaN                  NaN   
2693                      NaN                        NaN                  NaN   
2597                 0.128929                   4.900000             0.009009   
2650                 0.067645                   2.433333             0.088889   
2609                 0.009805                  -0.021429             0.000000   

      TargetShareMean_Last3  FantasyPointsMean_Last3  RushShareMean_Last5  \
19                      NaN                      NaN                  NaN   
0                       NaN                      NaN                  NaN   
26                      NaN                      NaN                  NaN   
11                      NaN                      NaN                  NaN   
13                      NaN                      NaN                  NaN   
...                     ...         

In [130]:
NewNewTE2020

PlayerID              Name Position  Week Team Opponent  Attempts  \
2        16964     Darren Waller       TE     1   LV      BAL         0   
13       10974    Rob Gronkowski       TE     1   TB      DAL         0   
5        20805    T.J. Hockenson       TE     1  DET       SF         0   
0        15048      Travis Kelce       TE     1   KC      CLE         0   
32       21738     Juwan Johnson       TE     1   NO       GB         0   
...        ...               ...      ...   ...  ...      ...       ...   
1527     20134       Kevin Rader       TE    17  PIT      CLE         0   
1541     20199       David Wells       TE    17  ARI      DAL         0   
1539     21865  Stephen Sullivan       TE    17  CAR       NO         0   
1489     21676     Jared Pinkney       TE    17  DET      SEA         0   
1540     22663  Hunter Kampmoyer       TE    17  LAC      DEN         0   

      RushShare  Targets  TargetShare  OPR  Salary  FantasyPoints  \
2           0.0       19     0.365385   10  7500.0           29.5   
13          0.0        8     0.173913   16  3900.0           29.0   
5           0.0       10     0.178571    1  4900.0           25.7   
0           0.0        7     0.212121   28  8300.0           25.6   
32          0.0        3     0.150000    4  3000.0           17.1   
...         ...      ...          ...  ...     ...            ...   
1527        0.0        0     0.000000   22  2500.0            0.0   
1541        0.0        0     0.000000   21  2500.0            0.0   
1539        0.0        0     0.000000    8  2500.0            0.0   
1489        0.0        0     0.000000   28  2500.0            0.0   
1540        0.0        0     0.000000    3  2500.0            0.0   

      FantasyPoints_DraftKingsProjection  RushShareMean_Rolling  \
2                                  16.43                    NaN   
13                                  8.79                    NaN   
5                                  12.61                    NaN   
0                                  20.12                    NaN   
32                                  5.80                    NaN   
...                                  ...                    ...   
1527                                0.65                    0.0   
1541                                0.00                    0.0   
1539                                0.00                    0.0   
1489                                4.00                    NaN   
1540                                0.00                    NaN   

      TargetShareMean_Rolling  FantasyPointsMean_Rolling  RushShareMean_Last3  \
2                         NaN                        NaN                  NaN   
13                        NaN                        NaN                  NaN   
5                         NaN                        NaN                  NaN   
0                         NaN                        NaN                  NaN   
32                        NaN                        NaN                  NaN   
...                       ...                        ...                  ...   
1527                 0.021164                        0.7                  0.0   
1541                 0.000000                        0.0                  NaN   
1539                 0.023256                        0.0                  NaN   
1489                      NaN                        NaN                  NaN   
1540                      NaN                        NaN                  NaN   

      TargetShareMean_Last3  FantasyPointsMean_Last3  RushShareMean_Last5  \
2                       NaN                      NaN                  NaN   
13                      NaN                      NaN                  NaN   
5                       NaN                      NaN                  NaN   
0                       NaN                      NaN                  NaN   
32                      NaN                      NaN                  NaN   
...                     ...         

In [131]:
NewNewQB2020.to_csv("~/Desktop/MGSC 434 Final Project/Regression data/QB2021.csv")
NewNewRB2020.to_csv("~/Desktop/MGSC 434 Final Project/Regression data/RB2021.csv")
NewNewWR2020.to_csv("~/Desktop/MGSC 434 Final Project/Regression data/WR2021.csv")
NewNewTE2020.to_csv("~/Desktop/MGSC 434 Final Project/Regression data/TE2021.csv")

### DST

In [132]:
### Load Datasets
StatsDST2020 = pd.read_csv("StatsDST2021.csv")
SalariesDST2020 = pd.read_csv("SalariesDST2021.csv")

In [133]:
### Merge DataFrames (DST)
selected_columns = ['PlayerID','Name_x','Position_x','Week','Team_x','Opponent_x','DraftKingsSalary','FantasyPointsDraftKings_y','FantasyPointsDraftKings_x']
renamed_columns = ['PlayerID','Name','Position','Week','Team','Opponent','Salary','FantasyPoints','FantasyPoints_DraftKingsProjection']

DST2020 = pd.merge(SalariesDST2020, StatsDST2020, how="inner", left_on=["PlayerID", "Week"], right_on=["PlayerID", "Week"])
DST2020 = DST2020[selected_columns]
DST2020.columns = renamed_columns

DST2020 = DST2020.sort_values(by=['Week','FantasyPoints'], ascending=[True, False])

In [134]:
DST2020

PlayerID                  Name Position  Week Team Opponent  Salary  \
23          1     Arizona Cardinals      DST     1  ARI      TEN  2100.0   
29         69    New Orleans Saints      DST     1   NO       GB  2200.0   
18         28   Pittsburgh Steelers      DST     1  PIT      BUF  2800.0   
0          93   San Francisco 49ers      DST     1   SF      DET  4200.0   
21         26   Philadelphia Eagles      DST     1  PHI      ATL  2600.0   
..        ...                   ...      ...   ...  ...      ...     ...   
500        49        Denver Broncos      DST    17  DEN      LAC  2600.0   
503         7    Cincinnati Bengals      DST    17  CIN       KC  2900.0   
506        11         Detroit Lions      DST    17  DET      SEA  2400.0   
505        67     Minnesota Vikings      DST    17  MIN       GB  2500.0   
509        52  Jacksonville Jaguars      DST    17  JAX       NE  2400.0   

     FantasyPoints  FantasyPoints_DraftKingsProjection  
23              16                                 6.7  
29              15                                 6.0  
18              14                                 7.3  
0               10                                 9.5  
21              10                                 7.2  
..             ...                                 ...  
500             -1                                 6.3  
503             -1                                 5.6  
506             -3                                 5.0  
505             -4                                 5.4  
509             -4                                 4.3  

[512 rows x 9 columns]

In [135]:
def averages_for(df):

    unique_teams = df.Team.unique()

    frames = []

    for x in unique_teams:

        team_df = df[df.Team==x]

        ####### ROLLING MEAN #######

        fantasy_points_mean = [np.nan]
        for i in range(1,len(team_df)+1):
            data_i = team_df.iloc[0:i]
            fantasy_points_mean.append(data_i.FantasyPoints.mean())
        team_df['FantasyPointsFor_MeanRolling'] = fantasy_points_mean[:-1]

        ####### LAST 3 GAMES MEAN #######

        if len(team_df) <= 3:
            fantasy_points_mean = [np.nan]*len(team_df)
            team_df['FantasyPointsMeanFor_Last3'] = fantasy_points_mean

        else:
            fantasy_points_mean = [np.nan]*3
            for i in range(len(team_df)-3):
                data_i = team_df.iloc[0+i:3+i]
                fantasy_points_mean.append(data_i.FantasyPoints.mean())
            team_df['FantasyPointsFor_MeanLast3'] = fantasy_points_mean

        ####### LAST 5 GAMES MEAN #######

        if len(team_df) <= 5:
            fantasy_points_mean = [np.nan]*len(team_df)
            team_df['FantasyPointsMeanFor_Last5'] = fantasy_points_mean

        else:
            fantasy_points_mean = [np.nan]*5
            for i in range(len(team_df)-5):
                data_i = team_df.iloc[0+i:5+i]
                fantasy_points_mean.append(data_i.FantasyPoints.mean())
            team_df['FantasyPointsFor_MeanLast5'] = fantasy_points_mean
            
        frames.append(team_df)

    final_df = pd.concat(frames)
    df_final = final_df.sort_values(by=['Week','FantasyPoints'], ascending=[True, False])
    return df_final

In [136]:
def averages_against(df):

    unique_opponets = df.Opponent.unique()

    frames = []

    for x in unique_opponets:

        opponent_df = df[df.Opponent==x]

        ####### ROLLING MEAN #######

        fantasy_points_mean = [np.nan]
        for i in range(1,len(opponent_df)+1):
            data_i = opponent_df.iloc[0:i]
            fantasy_points_mean.append(data_i.FantasyPoints.mean())
        opponent_df['FantasyPointsAgainst_MeanRolling'] = fantasy_points_mean[:-1]

        ####### LAST 3 GAMES MEAN #######

        if len(opponent_df) <= 3:
            fantasy_points_mean = [np.nan]*len(opponent_df)
            opponent_df['FantasyPointsMeanAgainst_Last3'] = fantasy_points_mean

        else:
            fantasy_points_mean = [np.nan]*3
            for i in range(len(opponent_df)-3):
                data_i = opponent_df.iloc[0+i:3+i]
                fantasy_points_mean.append(data_i.FantasyPoints.mean())
            opponent_df['FantasyPointsAgainst_MeanLast3'] = fantasy_points_mean

        ####### LAST 5 GAMES MEAN #######

        if len(opponent_df) <= 5:
            fantasy_points_mean = [np.nan]*len(opponent_df)
            opponent_df['FantasyPointsMeanAgainst_Last5'] = fantasy_points_mean

        else:
            fantasy_points_mean = [np.nan]*5
            for i in range(len(opponent_df)-5):
                data_i = opponent_df.iloc[0+i:5+i]
                fantasy_points_mean.append(data_i.FantasyPoints.mean())
            opponent_df['FantasyPointsAgainst_MeanLast5'] = fantasy_points_mean
            
        frames.append(opponent_df)

    final_df = pd.concat(frames)
    df_final = final_df.sort_values(by=['Week','FantasyPoints'], ascending=[True, False])
    return df_final        

In [137]:
DSTFor = averages_for(DST2020)
DSTAgainst = averages_against(DST2020)

<ipython-input-135-69e0dd3111be>:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_df['FantasyPointsFor_MeanRolling'] = fantasy_points_mean[:-1]
<ipython-input-135-69e0dd3111be>:30: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_df['FantasyPointsFor_MeanLast3'] = fantasy_points_mean
<ipython-input-135-69e0dd3111be>:43: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentat

In [138]:
pd.merge(DSTFor, DSTAgainst, how="inner", left_on=["PlayerID", "Week"], right_on=["PlayerID", "Week"])

PlayerID                Name_x Position_x  Week Team_x Opponent_x  \
0           1     Arizona Cardinals        DST     1    ARI        TEN   
1          69    New Orleans Saints        DST     1     NO         GB   
2          28   Pittsburgh Steelers        DST     1    PIT        BUF   
3          93   San Francisco 49ers        DST     1     SF        DET   
4          26   Philadelphia Eagles        DST     1    PHI        ATL   
..        ...                   ...        ...   ...    ...        ...   
507        49        Denver Broncos        DST    17    DEN        LAC   
508         7    Cincinnati Bengals        DST    17    CIN         KC   
509        11         Detroit Lions        DST    17    DET        SEA   
510        67     Minnesota Vikings        DST    17    MIN         GB   
511        52  Jacksonville Jaguars        DST    17    JAX         NE   

     Salary_x  FantasyPoints_x  FantasyPoints_DraftKingsProjection_x  \
0      2100.0               16                                   6.7   
1      2200.0               15                                   6.0   
2      2800.0               14                                   7.3   
3      4200.0               10                                   9.5   
4      2600.0               10                                   7.2   
..        ...              ...                                   ...   
507    2600.0               -1                                   6.3   
508    2900.0               -1                                   5.6   
509    2400.0               -3                                   5.0   
510    2500.0               -4                                   5.4   
511    2400.0               -4                                   4.3   

     FantasyPointsFor_MeanRolling  FantasyPointsFor_MeanLast3  \
0                             NaN                         NaN   
1                             NaN                         NaN   
2                             NaN                         NaN   
3                             NaN                         NaN   
4                             NaN                         NaN   
..                            ...                         ...   
507                      7.933333                    7.666667   
508                      6.533333                    5.666667   
509                      3.466667                    3.666667   
510                      7.400000                    8.666667   
511                      3.800000                    4.666667   

     FantasyPointsFor_MeanLast5                Name_y Position_y Team_y  \
0                           NaN     Arizona Cardinals        DST    ARI   
1                           NaN    New Orleans Saints        DST     NO   
2                           NaN   Pittsburgh Steelers        DST    PIT   
3                           NaN   San Francisco 49ers        DST     SF   
4                           NaN   Philadelphia Eagles        DST    PHI   
..                          ...                   ...        ...    ...   
507                         8.8        Denver Broncos        DST    DEN   
508                         8.4    Cincinnati Bengals        DST    CIN   
509                         4.0         Detroit Lions        DST    DET   
510                         8.2     Minnesota Vikings        DST    MIN   
511                         3.2  Jacksonville Jaguars        DST    JAX   

    Opponent_y  Salary_y  FantasyPoints_y  \
0          TEN    2100.0               16   
1           GB    2200.0               15   
2          BUF    2800.0               14   
3          DET    4200.0               10   
4          ATL    2600.0               10   
..         ...       ...              ...   
507        LAC    2600.0               -1   
508         KC    2900.0               -1   
509        SEA    2400.0               -3   
510         GB    2500.0               -4   
511         NE    2400.0               -4   

     FantasyPoints_DraftKing

In [139]:
### Merge DataFrames (DSTFor, DSTAgainst)
selected_columns = ['PlayerID','Name_x','Position_x','Week','Team_x','Opponent_x','Salary_x','FantasyPoints_x','FantasyPoints_DraftKingsProjection_x','FantasyPointsFor_MeanRolling','FantasyPointsFor_MeanLast3','FantasyPointsFor_MeanLast5','FantasyPointsAgainst_MeanRolling','FantasyPointsAgainst_MeanLast3','FantasyPointsAgainst_MeanLast5']
renamed_columns = ['PlayerID','Name','Position','Week','Team','Opponent','Salary','FantasyPoints','FantasyPoints_DraftKingsProjection','FantasyPointsFor_MeanRolling','FantasyPointsFor_MeanLast3','FantasyPointsFor_MeanLast5','FantasyPointsAgainst_MeanRolling','FantasyPointsAgainst_MeanLast3','FantasyPointsAgainst_MeanLast5']

DST2020 = pd.merge(DSTFor, DSTAgainst, how="inner", left_on=["PlayerID", "Week"], right_on=["PlayerID", "Week"])
DST2020 = DST2020[selected_columns]
DST2020.columns = renamed_columns

DST2020 = DST2020.sort_values(by=['Week','FantasyPoints'], ascending=[True, False])

In [140]:
DST2020

PlayerID                  Name Position  Week Team Opponent  Salary  \
0           1     Arizona Cardinals      DST     1  ARI      TEN  2100.0   
1          69    New Orleans Saints      DST     1   NO       GB  2200.0   
2          28   Pittsburgh Steelers      DST     1  PIT      BUF  2800.0   
3          93   San Francisco 49ers      DST     1   SF      DET  4200.0   
4          26   Philadelphia Eagles      DST     1  PHI      ATL  2600.0   
..        ...                   ...      ...   ...  ...      ...     ...   
507        49        Denver Broncos      DST    17  DEN      LAC  2600.0   
508         7    Cincinnati Bengals      DST    17  CIN       KC  2900.0   
509        11         Detroit Lions      DST    17  DET      SEA  2400.0   
510        67     Minnesota Vikings      DST    17  MIN       GB  2500.0   
511        52  Jacksonville Jaguars      DST    17  JAX       NE  2400.0   

     FantasyPoints  FantasyPoints_DraftKingsProjection  \
0               16                                 6.7   
1               15                                 6.0   
2               14                                 7.3   
3               10                                 9.5   
4               10                                 7.2   
..             ...                                 ...   
507             -1                                 6.3   
508             -1                                 5.6   
509             -3                                 5.0   
510             -4                                 5.4   
511             -4                                 4.3   

     FantasyPointsFor_MeanRolling  FantasyPointsFor_MeanLast3  \
0                             NaN                         NaN   
1                             NaN                         NaN   
2                             NaN                         NaN   
3                             NaN                         NaN   
4                             NaN                         NaN   
..                            ...                         ...   
507                      7.933333                    7.666667   
508                      6.533333                    5.666667   
509                      3.466667                    3.666667   
510                      7.400000                    8.666667   
511                      3.800000                    4.666667   

     FantasyPointsFor_MeanLast5  FantasyPointsAgainst_MeanRolling  \
0                           NaN                               NaN   
1                           NaN                               NaN   
2                           NaN                               NaN   
3                           NaN                               NaN   
4                           NaN                               NaN   
..                          ...                               ...   
507                         8.8                          5.333333   
508                         8.4                          5.466667   
509                         4.0                          5.933333   
510                         8.2                          3.933333   
511                         3.2                          5.933333   

     FantasyPointsAgainst_MeanLast3  FantasyPointsAgainst_MeanLast5  
0                               NaN                             NaN  
1                               NaN                             NaN  
2                               NaN                             NaN  
3                               NaN                             NaN  
4                               NaN                             NaN  
..                              ...                             ...  
507                        4.333333                             7.2  
508                        0.333333                             2.6  
509                        3.333333                             5.4  
510                        2.333333                             2.0  
511            

In [141]:
def injuries_DST(df):
    
    QBInjuries = []
    RBInjuries = []
    WRInjuries = []
    TEInjuries = []

    for i in range(len(df)):

        row_active = df.iloc[i,]

        injury_df = Injuries2020[(Injuries2020.Team == row_active.Opponent)&(Injuries2020.Week == row_active.Week)]

        QBInjured = 0
        RBInjured = 0
        WRInjured = 0
        TEInjured = 0

        for row_injured in range(len(injury_df)):

            name = injury_df.Name.iloc[row_injured,]
            week = injury_df.Week.iloc[row_injured,]
            position = injury_df.Position.iloc[row_injured,]
            team = injury_df.Team.iloc[row_injured,]

            if position == 'QB':
                int_df = NewQB2020[(NewQB2020.Team == team)&(NewQB2020.Week < week)].reset_index()
                if len(int_df) != 0:
                    a_fpms = []
                    for j in int_df.Name.unique():
                        qb_j = int_df[int_df.Name == j]
                        most_recent = qb_j.iloc[len(qb_j)-1,]
                        a_fpm = most_recent.FantasyPointsMean_Rolling
                        if math.isnan(a_fpm) == True:
                            a_fpm = 0
                        a_fpms.append(a_fpm)
                        
                    index = a_fpms.index(max(a_fpms))
                    if int_df.Name.unique()[index] == name:
                        QBInjured += 1

            elif position == 'RB':
                int_df = NewRB2020[(NewRB2020.Name == name)&(NewRB2020.Week < week)].reset_index()
                if len(int_df) != 0:
                    most_recent = int_df.iloc[len(int_df)-1,]
                    i_fpm = most_recent.FantasyPointsMean_Rolling
                    flexes = NewFLEX2020[(NewFLEX2020.Team == team)&(NewFLEX2020.Week < week)]
                    relevant_flexes = flexes[flexes.FantasyPointsMean_Rolling > 0]
                    avg_fpm = relevant_flexes.FantasyPointsMean_Rolling.mean()
                    if i_fpm >= avg_fpm:
                        RBInjured += 1

            elif position == 'WR':
                int_df = NewWR2020[(NewWR2020.Name == name)&(NewWR2020.Week < week)].reset_index()
                if len(int_df) != 0:
                    most_recent = int_df.iloc[len(int_df)-1,]
                    i_fpm = most_recent.FantasyPointsMean_Rolling
                    flexes = NewFLEX2020[(NewFLEX2020.Team == team)&(NewFLEX2020.Week < week)]
                    relevant_flexes = flexes[flexes.FantasyPointsMean_Rolling > 0]
                    avg_fpm = relevant_flexes.FantasyPointsMean_Rolling.mean()
                    if i_fpm >= avg_fpm:
                        WRInjured += 1

            elif position == 'TE':
                int_df = NewTE2020[(NewTE2020.Team == team)&(NewTE2020.Week < week)].reset_index()
                if len(int_df) != 0:
                    a_fpms = []
                    for j in int_df.Name.unique():
                        te_j = int_df[int_df.Name == j]
                        most_recent = te_j.iloc[len(te_j)-1,]
                        a_fpm = most_recent.FantasyPointsMean_Rolling
                        if math.isnan(a_fpm) == True:
                            a_fpm = 0
                        a_fpms.append(a_fpm)
                    index = a_fpms.index(max(a_fpms))
                    if int_df.Name.unique()[index] == name:
                        TEInjured += 1


        QBInjuries.append(QBInjured)
        RBInjuries.append(RBInjured)
        WRInjuries.append(WRInjured)
        TEInjuries.append(TEInjured)

    df['QBInjured'] = QBInjuries
    df['RBInjured'] = RBInjuries
    df['WRInjured'] = WRInjuries
    df['TEInjured'] = TEInjuries
    return df

In [142]:
NewDST2020 = injuries_DST(DST2020)

In [143]:
NewDST2020

PlayerID                  Name Position  Week Team Opponent  Salary  \
0           1     Arizona Cardinals      DST     1  ARI      TEN  2100.0   
1          69    New Orleans Saints      DST     1   NO       GB  2200.0   
2          28   Pittsburgh Steelers      DST     1  PIT      BUF  2800.0   
3          93   San Francisco 49ers      DST     1   SF      DET  4200.0   
4          26   Philadelphia Eagles      DST     1  PHI      ATL  2600.0   
..        ...                   ...      ...   ...  ...      ...     ...   
507        49        Denver Broncos      DST    17  DEN      LAC  2600.0   
508         7    Cincinnati Bengals      DST    17  CIN       KC  2900.0   
509        11         Detroit Lions      DST    17  DET      SEA  2400.0   
510        67     Minnesota Vikings      DST    17  MIN       GB  2500.0   
511        52  Jacksonville Jaguars      DST    17  JAX       NE  2400.0   

     FantasyPoints  FantasyPoints_DraftKingsProjection  \
0               16                                 6.7   
1               15                                 6.0   
2               14                                 7.3   
3               10                                 9.5   
4               10                                 7.2   
..             ...                                 ...   
507             -1                                 6.3   
508             -1                                 5.6   
509             -3                                 5.0   
510             -4                                 5.4   
511             -4                                 4.3   

     FantasyPointsFor_MeanRolling  FantasyPointsFor_MeanLast3  \
0                             NaN                         NaN   
1                             NaN                         NaN   
2                             NaN                         NaN   
3                             NaN                         NaN   
4                             NaN                         NaN   
..                            ...                         ...   
507                      7.933333                    7.666667   
508                      6.533333                    5.666667   
509                      3.466667                    3.666667   
510                      7.400000                    8.666667   
511                      3.800000                    4.666667   

     FantasyPointsFor_MeanLast5  FantasyPointsAgainst_MeanRolling  \
0                           NaN                               NaN   
1                           NaN                               NaN   
2                           NaN                               NaN   
3                           NaN                               NaN   
4                           NaN                               NaN   
..                          ...                               ...   
507                         8.8                          5.333333   
508                         8.4                          5.466667   
509                         4.0                          5.933333   
510                         8.2                          3.933333   
511                         3.2                          5.933333   

     FantasyPointsAgainst_MeanLast3  FantasyPointsAgainst_MeanLast5  \
0                               NaN                             NaN   
1                               NaN                             NaN   
2                               NaN                             NaN   
3                               NaN                             NaN   
4                               NaN                             NaN   
..                              ...                             ...   
507                        4.333333                             7.2   
508                        0.333333                             2.6   
509                        3.333333                             5.4   
510                        2.333333                             2.0   
511 

In [144]:
NewDST2020.to_csv("~/Desktop/MGSC 434 Final Project/Regression data/DST2021.csv")